In [ ]:
# download DEMs

In [1]:
#!mamba install -y -c conda-forge py3dep=0.13.0 
!pip install py3dep

  Using cached py3dep-0.13.10-py3-none-any.whl (22 kB)
  Using cached pygeoutils-0.13.11-py3-none-any.whl (21 kB)
  Using cached async_retriever-0.3.10-py3-none-any.whl (16 kB)
  Using cached pygeoogc-0.13.10-py3-none-any.whl (33 kB)
  Using cached aiohttp-3.8.3-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (1.0 MB)
  Using cached ujson-5.7.0-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (52 kB)
  Using cached aiohttp_client_cache-0.8.1-py3-none-any.whl (31 kB)
  Using cached url_normalize-1.4.3-py2.py3-none-any.whl (6.8 kB)
  Using cached OWSLib-0.27.2-py2.py3-none-any.whl (218 kB)
  Using cached requests_cache-0.9.8-py3-none-any.whl (48 kB)
  Using cached loguru-0.6.0-py3-none-any.whl (58 kB)
  Using cached itsdangerous-2.1.2-py3-none-any.whl (15 kB)
  Using cached python_forge-18.6.0-py35-none-any.whl (31 kB)
  Using cached aiodns-3.0.0-py3-none-any.whl (5.0 kB)
  Using cached Brotli-1.0.9-cp310-cp310-manylinux_2_5_x86_64.manylinux1_x86_64.manylinux_2_12_x8

In [2]:
import numpy as np
import pandas as pd
import geopandas as gpd
import rasterio as rio
import pystac
import pystac_client
import stackstac
import matplotlib.pyplot as plt
import xarray as xr
from datetime import datetime
import matplotlib
import ipyleaflet
import sys
import os
import dask_gateway
import planetary_computer
from rechunker import rechunk
sys.path.append('../sar_snowmelt_timing')
import s1_rtc_bs_utils
import contextily as ctx
import rioxarray as rxr
import skimage
import pathlib
import glob
import re

In [3]:
import py3dep

In [6]:
names = ['MtBaker',
         'GlacierPeak',
         'MtRainier',
         'MtAdams',
         'MtStHelens',
         'MtHood',
         'MtJefferson',
         'ThreeSisters',
         #'CraterLake',
         'MtShasta',
         'LassenPeak',]

geojsons = ['../input/shapefiles/mt_baker.geojson',
            '../input/shapefiles/glacier_peak.geojson',
            '../input/shapefiles/mt_rainier.geojson',
            '../input/shapefiles/mt_adams.geojson',
            '../input/shapefiles/mt_st_helens.geojson',
            '../input/shapefiles/mt_hood.geojson',
            '../input/shapefiles/mt_jefferson.geojson',
            '../input/shapefiles/three_sisters.geojson',
            #'../input/shapefiles/crater_lake.geojson',
            '../input/shapefiles/mt_shasta.geojson',
            '../input/shapefiles/lassen_peak.geojson',]

In [4]:
names = ['Olympics']
geojsons = ['../input/shapefiles/olympics.geojson']

In [5]:
classes = [ # page 13 of https://esa-worldcover.s3.amazonaws.com/v100/2020/docs/WorldCover_PUM_V1.0.pdf
#    10, # treecover
    20, # shrubland
    30, # grassland
    40, # cropland
#    50, # built-up
    60, #bare / sparse vegetation
    70, # snow and ice
#    80, # permanent water bodies
    90, # herbaceous wetlands
    95, # mangroves
    100 # loss and lichen
]

In [6]:
for nm, gj in zip(names,geojsons):
    print(f'Processing {nm}:')
    bbox_gdf = gpd.read_file(gj)
    ts_ds = s1_rtc_bs_utils.get_s1_rtc_stac_pc(bbox_gdf,start_time='2019-01-01',end_time='2019-01-30',polarization='vv',resolution=10)
    worldcover = s1_rtc_bs_utils.get_worldcover(ts_ds)
    ts_ds = ts_ds.where(worldcover.isin(classes))
    dem = s1_rtc_bs_utils.get_py3dep_dem(ts_ds)
    aspect = s1_rtc_bs_utils.get_py3dep_aspect(ts_ds)
    slope = s1_rtc_bs_utils.get_py3dep_slope(ts_ds)
    
    dem.rio.to_raster(f'../output/{nm}/dem_{nm}_10m.tif')
    aspect.rio.to_raster(f'../output/{nm}/aspect_{nm}_10m.tif')
    slope.rio.to_raster(f'../output/{nm}/slope_{nm}_10m.tif')
    

Processing Olympics:


/srv/conda/envs/notebook/lib/python3.10/site-packages/dask/array/reductions.py:586: RuntimeWarning: All-NaN slice encountered
  return np.nanmin(x_chunk, axis=axis, keepdims=keepdims)
